<h1 align=center><font size = 5>Restaurant Clusters in Berlin</font></h1>

## Introduction

In this project, we will explore popular restaurants in Berlin, Germany and then find out in which regions they are particularly clustered via the DBSCAN algorithm.

Our goal is to determine which areas have dense clusters that sustain an efficient food delivery network.

Before we get the data and start exploring it, let's import all the libraries we will need.

In [1]:
import requests
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import numpy as np
import folium
from folium import plugins
from folium.plugins import HeatMap
from folium.plugins import FastMarkerCluster
from folium.features import DivIcon
import json
from functools import partial
from geopy.geocoders import Nominatim
from sklearn.cluster import DBSCAN

## 1. Create a Grid Over Berlin

When exploring recommended venues near a given location, Foursquare API [limits](https://developer.foursquare.com/docs/api-reference/venues/explore/#parameters) the number of results. Since we would like to explore a large part of Berlin's city center, simply exploring the city from one location will not give us enough data points. As a solution we can create a grid of locations and explore each location separately to get a comprehensive view of the city.

To start, we determine south-western and north-western edges of the grid we would like to work with as well as the vertical and horizontal coordinate distances between each point in the grid.

In [2]:
lat_limit_south, lon_limit_west = 52.490, 13.30
lat_limit_north, lon_limit_east = 52.532, 13.45
lat_stride = 0.006 # around 670 meters
lon_stride = 0.01

Having done it, we can also quickly save the center point of the grid which will later be useful when visualizing the city map.

In [3]:
lat_center = (lat_limit_south+ lat_limit_north) / 2
lon_center = (lon_limit_west + lon_limit_east) / 2

We get all of the grid points by starting from the southwestern corner and jumping in our pre-determined step distances until we reach the northwestern edge.

In [4]:
def create_grid(lat_limit_north, lon_limit_west, lat_limit_south, lon_limit_east, lat_stride, lon_stride):
    grid = []
    lat_steps = round((lat_limit_north - lat_limit_south)/lat_stride) + 1
    lon_steps = round((lon_limit_east - lon_limit_west)/lon_stride) + 1
    for lat in np.linspace(lat_limit_south, lat_limit_north, num=lat_steps):
        for lon in np.linspace(lon_limit_west, lon_limit_east, num=lon_steps):
            coord = (round(lat, 3), round(lon, 3))
            grid.append(coord)
    return grid

berlin_grid = create_grid(lat_limit_north, lon_limit_west, lat_limit_south, lon_limit_east, lat_stride, lon_stride)
berlin_grid

[(52.49, 13.3),
 (52.49, 13.31),
 (52.49, 13.32),
 (52.49, 13.33),
 (52.49, 13.34),
 (52.49, 13.35),
 (52.49, 13.36),
 (52.49, 13.37),
 (52.49, 13.38),
 (52.49, 13.39),
 (52.49, 13.4),
 (52.49, 13.41),
 (52.49, 13.42),
 (52.49, 13.43),
 (52.49, 13.44),
 (52.49, 13.45),
 (52.496, 13.3),
 (52.496, 13.31),
 (52.496, 13.32),
 (52.496, 13.33),
 (52.496, 13.34),
 (52.496, 13.35),
 (52.496, 13.36),
 (52.496, 13.37),
 (52.496, 13.38),
 (52.496, 13.39),
 (52.496, 13.4),
 (52.496, 13.41),
 (52.496, 13.42),
 (52.496, 13.43),
 (52.496, 13.44),
 (52.496, 13.45),
 (52.502, 13.3),
 (52.502, 13.31),
 (52.502, 13.32),
 (52.502, 13.33),
 (52.502, 13.34),
 (52.502, 13.35),
 (52.502, 13.36),
 (52.502, 13.37),
 (52.502, 13.38),
 (52.502, 13.39),
 (52.502, 13.4),
 (52.502, 13.41),
 (52.502, 13.42),
 (52.502, 13.43),
 (52.502, 13.44),
 (52.502, 13.45),
 (52.508, 13.3),
 (52.508, 13.31),
 (52.508, 13.32),
 (52.508, 13.33),
 (52.508, 13.34),
 (52.508, 13.35),
 (52.508, 13.36),
 (52.508, 13.37),
 (52.508, 13.38

In [5]:
print("The grid has", len(berlin_grid), "coordinates!")

The grid has 128 coordinates!


We now have a grid of 128 coordinate points that should span the central part of Berlin.

Let's visualize a `Folium` map of the grid to make sure! We center the map on the middle coordinates and select an apropriate zoom level. Afterwards we add each location point of the grid to be visualized on this map.

In [6]:
# initiate new map
map_berlin = folium.Map(location=[lat_center, lon_center], zoom_start=13
                       )

# add markers to map
for coord in berlin_grid:
    lat = coord[0]
    lon = coord[1]
    label = '{}, {}'.format(lat, lon)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_berlin) 

# show map
map_berlin

As can be seen, our grid covers a good portion of the city center. Moreover, we can easily make this covered grid area larger or smaller as needed by changing the edge points of the grid.

## 2. Get Restaurant Data from Foursquare

We will need to use our developer account credentials to interact with the Foursquare API. However, it isn't a good security practice to include this confidential data in a public notebook. Our solution is store the credentials in a separate JSON file. You can see how we created this JSON with the commented out code below. Just uncomment and insert your *Client ID* and *Client Secret* if you would like to re-run the rest of the API calls yourself.

In [7]:
#data = {}
#data['client_id'] = []
#data['client_id'] = "YOUR CLIENT ID HERE"
#data['client_secret'] = []
#data['client_secret'] = "YOUR CLIENT SECRET HERE"

#with open('credentials.json', 'w') as outfile:
#    json.dump(data, outfile)

In [8]:
with open('credentials.json') as f:
    data = json.load(f)
    CLIENT_ID = data['client_id']
    CLIENT_SECRET = data['client_secret']

VERSION = '20180605'

#### Test Run

Let's make a test run and explore a single location's area.

We will use the `explore` endpoint on the location's coordinates to list most popular `food` venues within 500 metres. Beware that Foursquare's results change depending on the time of the day we run the query. Therefore, we use the `time` parameter so that the results correspond to any time of the day.

In [9]:
radius = 500
LIMIT = 100
latitude = 52.52
longitude = 13.40
section = 'food'
time = 'any'
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}&section={}&time={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT, section, time)
url

'https://api.foursquare.com/v2/venues/explore?client_id=424OFZHPYRYNX0JJ423PUY2LWXDBWDUVC2JBWRUWVZ5XGNM0&client_secret=5TA1SHLPTM0KWZYXVL4PVDX4GNZ44HTPVUDZZHISZEGW2W3N&ll=52.52,13.4&v=20180605&radius=500&limit=100&section=food&time=any'

In [10]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ede7ec1c94979001b4cd0cb'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Museumsinsel',
  'headerFullLocation': 'Museumsinsel, Berlin',
  'headerLocationGranularity': 'neighborhood',
  'query': 'food',
  'totalResults': 57,
  'suggestedBounds': {'ne': {'lat': 52.524500004500005,
    'lng': 13.4073816223365},
   'sw': {'lat': 52.5154999955, 'lng': 13.392618377663501}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '55031515498ecb9c699ed0a0',
       'name': 'Café 93',
       'location': {'address': 'Monbijouplatz 2',
        'lat': 52.52299702982836,
        'lng': 13.399751875666775,
        'labeledLatLngs': [{'label': 'display',
          '

The query seems to return a good number of results.

To be able to get a better sense of results and, later on, easily visualize and parse data, we will need to convert the results into a data frame.

In [11]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

As we don't need every field of data regarding the venues, we will retrieve just the unique ID number, Name, Category and coordinates into our dataframe.

In [12]:
venues = results['response']['groups'][0]['items']

nearby_venues = pd.json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.id', 'venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues = nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

Let's see how our data frame looks like by displaying the first 10 rows of it.

In [13]:
nearby_venues.head(10)

id                       name             categories  \
0  55031515498ecb9c699ed0a0                    Café 93                   Café   
1  59148ac8f2905e48f712375f           MA'LOA Poké Bowl             Poke Place   
2  54528ad2498e59da3cf912bf                    Dae Mon      Korean Restaurant   
3  5d440eb68e0eb70009db731c                     Kadoya    Japanese Restaurant   
4  4fa95dd5e4b09ce165996cd3                      Jolly     Chinese Restaurant   
5  4bf556ef6a31d13ae6bc962e                   Curry 61       Currywurst Joint   
6  5d31865fd1b9890007ade245      T2 Breakfast & Coffee         Breakfast Spot   
7  4bbf0bf4006dc9b60aeffb3f                  La Siesta                   Café   
8  59ac09a93d47914d453bc4f1  Quy Nguyen - Vegan Living  Vietnamese Restaurant   
9  4f92c347e4b04c0c9e914635          Rifugio De Napoli            Pizza Place   

         lat        lng  
0  52.522997  13.399752  
1  52.523653  13.400399  
2  52.522745  13.399324  
3  52.522844  13.400317  
4  52.520529  13.394801  
5  52.523637  13.400620  
6  52.521933  13.403187  
7  52.521960  13.401849  
8  52.523652  13.400528  
9  52.522759  13.394635

In [14]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

57 venues were returned by Foursquare.


We seem to have over 50 venues nearby for this location.

Let's define a function that explores a given location just like we did with the first sample location.

In [15]:
def explore_area(lat, lon):
    VERSION = '20180605'
    
    radius = 500
    LIMIT = 100
    latitude = lat
    longitude = lon
    section = 'food'
    time = 'any'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}&section={}&time={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, LIMIT, section, time)
    
    results = requests.get(url).json()
    
    if results['response']['totalResults'] > 0:
    
        venues = results['response']['groups'][0]['items']

        nearby_venues = pd.json_normalize(venues) # flatten JSON

        # filter columns
        filtered_columns = ['venue.id', 'venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
        nearby_venues = nearby_venues.loc[:, filtered_columns]

        # filter the category for each row
        nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

        # clean columns
        nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

        return nearby_venues
    else:
        return None

We can now run this function for every point in the grid and save the results in the `all_areas` dataframe.

Please note that since the search areas of the grid points somewhat overlap, we can receive duplicate venues between location searches. Therefore, we make sure a venue is not already listed in the dataframe before saving it thanks to the unique venue IDs.

In [16]:
column_names = ["id", "name", "categories", "lat", "lng"]
all_areas = pd.DataFrame(columns = column_names)

for coordinates in berlin_grid:
    lat = coordinates[0]
    lon = coordinates[1]
    
    # explore the grid area
    print("Exploring:", coordinates)
    area = explore_area(lat, lon)
    
    # make sure there is a venue in area
    if area is not None:
        # add venues that are not previously recorded to the master venue list
        for index, row in area.iterrows():
            if area.iloc[index].values[0] not in all_areas.values:
                all_areas = all_areas.append(area.iloc[index])

all_areas.reset_index(drop=True, inplace=True)
print("Finished exploring!")

Exploring: (52.49, 13.3)
Exploring: (52.49, 13.31)
Exploring: (52.49, 13.32)
Exploring: (52.49, 13.33)
Exploring: (52.49, 13.34)
Exploring: (52.49, 13.35)
Exploring: (52.49, 13.36)
Exploring: (52.49, 13.37)
Exploring: (52.49, 13.38)
Exploring: (52.49, 13.39)
Exploring: (52.49, 13.4)
Exploring: (52.49, 13.41)
Exploring: (52.49, 13.42)
Exploring: (52.49, 13.43)
Exploring: (52.49, 13.44)
Exploring: (52.49, 13.45)
Exploring: (52.496, 13.3)
Exploring: (52.496, 13.31)
Exploring: (52.496, 13.32)
Exploring: (52.496, 13.33)
Exploring: (52.496, 13.34)
Exploring: (52.496, 13.35)
Exploring: (52.496, 13.36)
Exploring: (52.496, 13.37)
Exploring: (52.496, 13.38)
Exploring: (52.496, 13.39)
Exploring: (52.496, 13.4)
Exploring: (52.496, 13.41)
Exploring: (52.496, 13.42)
Exploring: (52.496, 13.43)
Exploring: (52.496, 13.44)
Exploring: (52.496, 13.45)
Exploring: (52.502, 13.3)
Exploring: (52.502, 13.31)
Exploring: (52.502, 13.32)
Exploring: (52.502, 13.33)
Exploring: (52.502, 13.34)
Exploring: (52.502, 13

In [17]:
all_areas.head(10)

id                 name             categories  \
0  51b0b687498eb7911a3f5d5d               Viet's  Vietnamese Restaurant   
1  50083606e4b0a467c6a67a52             Il Gusto     Italian Restaurant   
2  515ad070e4b0e1f513fdb28b            Steinecke                 Bakery   
3  4b5c51f4f964a520dd2a29e3   Trattoria Taormina      Trattoria/Osteria   
4  4dd3a22cb0fbf653b6413b4c     Grillhaus Wedo's            Snack Place   
5  4e2680c93151a5765fc70e27          Wasserperle      German Restaurant   
6  51727692e4b093e579db5b55  Das Knusperhäuschen                 Bakery   
7  4f9fadd5e4b0f9485431228c           LECKERBACK                 Bakery   
8  56670809498eba82ce7def90            Genazvale   Caucasian Restaurant   
9  4b0919a7f964a5203d1423e3      Parkcafé Berlin                   Café   

         lat        lng  
0  52.486826  13.298148  
1  52.487640  13.299763  
2  52.493167  13.305096  
3  52.491707  13.301395  
4  52.488470  13.301182  
5  52.491629  13.299931  
6  52.491535  13.293843  
7  52.486170  13.297124  
8  52.489803  13.312004  
9  52.490966  13.314369

In [18]:
all_areas.shape

(2942, 5)

In [19]:
print('There are {} unique restaurant categories.'.format(len(all_areas['categories'].unique())))

There are 120 unique restaurant categories.


We have collected almost 3000 restaurants in 120 restaurant categories!

## 3. Visualize the Data

Before analyzing the data for clusters, let's visualize the collected venues locations on a map.

Since there are too many venues in a comparatively dense area, displaying a marker for each venue wouldn't give us a meaningful map. In such a situation, it's better to use marker clusters that we can zoom-in on and explore interactively. We use `FastMarkerCluster` to efficiently parse our large number of results quickly.

In [38]:
# initiate new map
map_berlin_venues = folium.Map(location=[lat_center, lon_center], zoom_start=13)


# add markers to map
map_berlin_venues.add_child(FastMarkerCluster(all_areas[['lat', 'lng']].values.tolist()))

# show map
map_berlin_venues

As an additional map type, it would be interesting to utilize a `HeatMap`, as this map type would give us a visual way to imagine the density clusters of restaurants.

In [21]:
heatmap_berlin = folium.Map(location=[lat_center, lon_center], zoom_start = 13) 

HeatMap(all_areas[['lat', 'lng']].values.tolist(), max_val=0.6, radius=21).add_to(heatmap_berlin)

heatmap_berlin

From this map, we can already see that restaurant concentration is low in parks and high in places near large train stations and shopping districts.

## 4. Create and Analyze Restaurant Clusters

Now that we have an idea of restaurant locations in the city center, we need to determine if and where there are dense clusters of venues. Our goal is to determine candidates for an area with an enough density of restaurants where we can offer a network of locally available riders as a home delivery solution for restaurants.

For this task, we don't choose traditional clustering methods such as k-means, hierarchical and fuzzy clustering. Even though they are good for determining areas with enough number of venues without supervision, they are not able to separate high density clusters from low-density areas.

Instead, we will use `DBSCAN` (Density-based spatial clustering of applications with noise) algorithm which can give us regions of high location density while separating low density locations as noise. We define density as having at least 60 restaurants within our specified radius.

In [22]:
db = DBSCAN(eps=0.006, min_samples=60).fit(all_areas[['lat','lng']])
labels = db.labels_
unique_labels = set(labels)

print(unique_labels)

{0, 1, 2, 3, 4, 5, -1}


DBSCAN found 6 clusters that fit our requirements. Please note that `-1` label is used for locations deemed noise, i.e. members of non-dense regions.

Let's save the region labels in our dataframe.

In [23]:
all_areas_regions = all_areas.copy()
all_areas_regions["Region"] = labels
all_areas_regions.head(20)

id                              name  \
0   51b0b687498eb7911a3f5d5d                            Viet's   
1   50083606e4b0a467c6a67a52                          Il Gusto   
2   515ad070e4b0e1f513fdb28b                         Steinecke   
3   4b5c51f4f964a520dd2a29e3                Trattoria Taormina   
4   4dd3a22cb0fbf653b6413b4c                  Grillhaus Wedo's   
5   4e2680c93151a5765fc70e27                       Wasserperle   
6   51727692e4b093e579db5b55               Das Knusperhäuschen   
7   4f9fadd5e4b0f9485431228c                        LECKERBACK   
8   56670809498eba82ce7def90                         Genazvale   
9   4b0919a7f964a5203d1423e3                   Parkcafé Berlin   
10  500e7a42e4b0a57241d8b10f                         Truc-xinh   
11  507feb4fe4b015eaecf999ea  Schlemmermarkt Fehrbeliner Platz   
12  519e2e97498e323cc612c0ee                   Café Milch Zeit   
13  58a04ec901f0772d803c209d                           Bahadur   
14  4bddb02b587b2d7f40ab5409                           A Telha   
15  4c66e091e75ac92853cff8da                           Paracas   
16  4e628839d164ddd5e5d21463         Restaurant  Zum Hax'nwirt   
17  4b609427f964a5208eee29e3                       Witwe Bolte   
18  4db1891d6e81a2637eed52fd       Les 3 veuves de Wilmersdorf   
19  4d9a03ab61a3a1cd227cf142                          Yoshioka   

                   categories        lat        lng  Region  
0       Vietnamese Restaurant  52.486826  13.298148      -1  
1          Italian Restaurant  52.487640  13.299763      -1  
2                      Bakery  52.493167  13.305096      -1  
3           Trattoria/Osteria  52.491707  13.301395      -1  
4                 Snack Place  52.488470  13.301182      -1  
5           German Restaurant  52.491629  13.299931      -1  
6                      Bakery  52.491535  13.293843      -1  
7                      Bakery  52.486170  13.297124      -1  
8        Caucasian Restaurant  52.489803  13.312004      -1  
9                        Café  52.490966  13.314369      -1  
10            Thai Restaurant  52.490150  13.314045      -1  
11                 Food Court  52.489933  13.314410      -1  
12                       Café  52.490984  13.316710      -1  
13          Indian Restaurant  52.487791  13.319595      -1  
14         Seafood Restaurant  52.490520  13.325013      -1  
15  Latin American Restaurant  52.491891  13.321121       0  
16          German Restaurant  52.491524  13.317790      -1  
17          German Restaurant  52.492500  13.323716       0  
18          French Restaurant  52.489290  13.319580      -1  
19        Japanese Restaurant  52.487990  13.317926      -1

At this point, it makes sense to visualize a map of our clusters (color markers) as well the noise (gray markers).

In [24]:
# initiate new map
map_berlin_regions = folium.Map(location=[lat_center, lon_center], zoom_start=13
                       )

colors = [
    'red',
    'blue',
    'purple',
    'orange',
    'green',
    'pink',
    'lightgreen',
    'darkblue',
    'lightblue',
    'darkred',
    'darkpurple',
    'darkgreen',
    'cadetblue',
    'beige'
]


# add markers to map
for index, row in all_areas_regions.iterrows():
    name = all_areas_regions.iloc[index].values[1]
    category = all_areas_regions.iloc[index].values[2]
    lat = all_areas_regions.iloc[index].values[3]
    lon = all_areas_regions.iloc[index].values[4]
    region = all_areas_regions.iloc[index].values[5]
    if region == -1:
        color = 'lightgray'
    else:
        color = colors[region]
    label = '{}'.format(category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=color,
        fill=True,
        #fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_berlin_regions) 

# show map
map_berlin_regions

To visualize the clusters more clearly, we can remove noise and label the region numbers on the map.

In [25]:
# initiate new map
map_berlin_regions = folium.Map(location=[lat_center, lon_center], zoom_start=13
                       )

# add markers to map
for index, row in all_areas_regions.iterrows():
    name = all_areas_regions.iloc[index].values[1]
    category = all_areas_regions.iloc[index].values[2]
    lat = all_areas_regions.iloc[index].values[3]
    lon = all_areas_regions.iloc[index].values[4]
    region = all_areas_regions.iloc[index].values[5]
    if region > -1:
        color = colors[region]
        label = '{}'.format(category)
        label = folium.Popup(label, parse_html=True)
        folium.CircleMarker(
            [lat, lon],
            radius=5,
            popup=label,
            color=color,
            fill=True,
            fill_opacity=0.7,
            parse_html=False).add_to(map_berlin_regions) 

    
for region in range(len(unique_labels)-1):
    lat = np.mean(all_areas_regions[all_areas_regions["Region"] == region].lat)
    lon = np.mean(all_areas_regions[all_areas_regions["Region"] == region].lng)
    folium.Marker(
        [lat, lon], 
        icon=DivIcon(
            icon_size=(150,36),
            icon_anchor=(10,24),
            html='<div style="font-size: 24pt; color : black; font-weight: bold">{}</div>'.format(region),
        )).add_to(map_berlin_regions)
    map_berlin_regions.add_child(folium.CircleMarker([lat, lon], radius=18, color='black'))

# show map
map_berlin_regions

Via the `geopy` library, we can get addresses of the geographical center (mean coordinates) of each region. In case, we'd want to service the region, we would prefer to have our service stations near these addresses.

In [26]:
for region in range(len(unique_labels)-1):
    llat = np.mean(all_areas_regions[all_areas_regions["Region"] == region].lat)
    llon = np.mean(all_areas_regions[all_areas_regions["Region"] == region].lng)
    geolocator = Nominatim(user_agent="foursquare")
    reverse = partial(geolocator.reverse, language="en")
    loc = str(llat) + ", " + str(llon)
    print("Center of Region", region, ":", reverse(loc)[0])

Center of Region 0 : 6, Meinekestraße, Charlottenburg, Charlottenburg-Wilmersdorf, 10719, Germany
Center of Region 1 : 107, Gneisenaustraße, Kreuzberg, Friedrichshain-Kreuzberg, Berlin, 10961, Germany
Center of Region 2 : 9, Lausitzer Straße, Kreuzberg, Friedrichshain-Kreuzberg, Berlin, 10999, Germany
Center of Region 3 : Pergamon Museum, 5, Am Kupfergraben, Spandauer Vorstadt, Mitte, Berlin, 10117, Germany
Center of Region 4 : Volkshochschule Mitte, Haus 3, 75, Turmstraße, Moabit, Mitte, Berlin, 10551, Germany
Center of Region 5 : Borowsky - der Ankleider, 27, Greifswalder Straße, Winsviertel, Prenzlauer Berg, Pankow, Berlin, 10405, Germany


The regions seem to have a varying number of locations in them.

In [27]:
berlin_regions = all_areas_regions[all_areas_regions['Region'] > -1]
berlin_regions.groupby('Region').count()[['id']]

id
Region     
0       690
1       182
2       407
3       875
4        62
5        72

Regions #3 and #0 have the most restaurants and region #4 barely made it into a dense cluster.

#### One Hot Encoding

Before deciding on a cluster based on member size, it would be best to compare the restaurant categories presented in the clusters, in case there is a significant discrepancy that could affect our decision.

To let python get us useful statistics, let's code category data into 0 & 1 for each category's presence in the regions.

In [28]:
# one hot encoding
berlin_regions_onehot = pd.get_dummies(berlin_regions[['categories']], prefix="", prefix_sep="")

# add region column back to dataframe
berlin_regions_onehot['Region'] = berlin_regions['Region']

# move region column to the first column
fixed_columns = [berlin_regions_onehot.columns[-1]] + list(berlin_regions_onehot.columns[:-1])
berlin_regions_onehot = berlin_regions_onehot[fixed_columns]

#berlin_regions_onehot['Count'] = berlin_regions.groupby('Region').count()[['id']].values

berlin_regions_onehot.head()

Region  African Restaurant  American Restaurant  Argentinian Restaurant  \
15       0                   0                    0                       0   
17       0                   0                    0                       0   
22       0                   0                    0                       0   
51       0                   0                    0                       0   
83       0                   1                    0                       0   

    Asian Restaurant  Australian Restaurant  Austrian Restaurant  BBQ Joint  \
15                 0                      0                    0          0   
17                 0                      0                    0          0   
22                 0                      0                    0          0   
51                 0                      0                    0          0   
83                 0                      0                    0          0   

    Bagel Shop  Bakery  Bavarian Restaurant  Bistro  Brasserie  \
15           0       0                    0       0          0   
17           0       0                    0       0          0   
22           0       0                    0       0          0   
51           0       0                    0       0          0   
83           0       0                    0       0          0   

    Bratwurst Joint  Brazilian Restaurant  Breakfast Spot  Buffet  \
15                0                     0               0       0   
17                0                     0               0       0   
22                0                     0               0       0   
51                0                     0               0       0   
83                0                     0               0       0   

    Burger Joint  Burrito Place  Cafeteria  Café  Campanian Restaurant  \
15             0              0          0     0                     0   
17             0              0          0     0                     0   
22             0              0          0     0                     0   
51             0              0          0     0                     0   
83             0              0          0     0                     0   

    Cantonese Restaurant  Caribbean Restaurant  Caucasian Restaurant  \
15                     0                     0                     0   
17                     0                     0                     0   
22                     0                     0                     0   
51                     0                     0                     0   
83                     0                     0                     0   

    Chinese Restaurant  Colombian Restaurant  Comfort Food Restaurant  \
15                   0                     0                        0   
17                   0                     0                        0   
22                   0                     0                        0   
51                   0                     0                        0   
83                   0                     0                        0   

    Creperie  Cuban Restaurant  Currywurst Joint  Deli / Bodega  \
15         0                 0                 0              0   
17         0                 0                 0              0   
22         0                 0                 0              0   
51         0                 0                 0              0   
83         0                 0                 0              0   

    Dim Sum Restaurant  Diner  Doner Restaurant  Donut Shop  \
15                   0      0                 0           0   
17                   0      0                 0           0   
22                   0      0                 0           0   
51                   0      0                 0           0   
83                   0      0                 0           0   

    Dumpling Restaurant  Eastern European Restaurant  Empanada Restaurant  \
15                    0                            0              

In [29]:
berlin_regions_onehot.shape

(2288, 117)

In [30]:
berlin_regions_grouped = berlin_regions_onehot.groupby('Region').mean().reset_index()
berlin_regions_grouped

Region  African Restaurant  American Restaurant  Argentinian Restaurant  \
0       0            0.001449             0.002899                0.002899   
1       1            0.010989             0.000000                0.005495   
2       2            0.009828             0.002457                0.002457   
3       3            0.000000             0.001143                0.001143   
4       4            0.000000             0.000000                0.000000   
5       5            0.000000             0.013889                0.000000   

   Asian Restaurant  Australian Restaurant  Austrian Restaurant  BBQ Joint  \
0          0.017391               0.000000             0.007246   0.001449   
1          0.043956               0.000000             0.010989   0.000000   
2          0.024570               0.000000             0.004914   0.004914   
3          0.022857               0.001143             0.000000   0.003429   
4          0.064516               0.000000             0.016129   0.016129   
5          0.027778               0.000000             0.013889   0.000000   

   Bagel Shop    Bakery  Bavarian Restaurant    Bistro  Brasserie  \
0    0.002899  0.066667             0.000000  0.005797   0.004348   
1    0.005495  0.060440             0.000000  0.027473   0.000000   
2    0.002457  0.061425             0.002457  0.019656   0.000000   
3    0.003429  0.070857             0.004571  0.025143   0.003429   
4    0.000000  0.112903             0.000000  0.000000   0.000000   
5    0.000000  0.055556             0.000000  0.000000   0.000000   

   Bratwurst Joint  Brazilian Restaurant  Breakfast Spot    Buffet  \
0         0.001449              0.000000        0.015942  0.001449   
1         0.000000              0.000000        0.016484  0.000000   
2         0.000000              0.000000        0.012285  0.000000   
3         0.000000              0.001143        0.026286  0.001143   
4         0.000000              0.000000        0.048387  0.000000   
5         0.000000              0.000000        0.041667  0.000000   

   Burger Joint  Burrito Place  Cafeteria      Café  Campanian Restaurant  \
0      0.026087       0.002899   0.001449  0.102899              0.000000   
1      0.021978       0.000000   0.000000  0.131868              0.000000   
2      0.022113       0.002457   0.000000  0.157248              0.002457   
3      0.018286       0.009143   0.004571  0.128000              0.000000   
4      0.064516       0.000000   0.000000  0.096774              0.000000   
5      0.027778       0.000000   0.013889  0.236111              0.000000   

   Cantonese Restaurant  Caribbean Restaurant  Caucasian Restaurant  \
0              0.000000              0.001449              0.004348   
1              0.000000              0.000000              0.000000   
2              0.002457              0.002457              0.002457   
3              0.000000              0.000000              0.002286   
4              0.000000              0.016129              0.000000   
5              0.000000              0.000000              0.000000   

   Chinese Restaurant  Colombian Restaurant  Comfort Food Restaurant  \
0            0.024638              0.000000                 0.001449   
1            0.000000              0.005495                 0.005495   
2            0.004914              0.000000                 0.000000   
3            0.011429              0.000000                 0.000000   
4            0.000000              0.000000                 0.000000   
5            0.013889              0.000000                 0.000000   

   Creperie  Cuban Restaurant  Currywurst Joint  Deli / Bodega  \
0  0.001449          0.001449          0.008696       0.005797   
1  0.005495          0.000000          0.010989       0.010989   
2  0.004914          0.000000          0.000000       0.007371   
3  0.000000          0.000000          0.012571       0.010286   
4  0.000000          0.000000          0.000000       0.00000

In [31]:
berlin_regions_grouped.shape

(6, 117)

We now have mean of the frequency of occurrence of each category in each region.

#### Most Common Restaurants in Each Cluster

We start with a function that can sort the restaurant categories in descending order.

In [32]:
# sort the venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create a new dataframe and populate with with the top 10 restaurant categoies for each region.

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Region']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Category'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Category'.format(ind+1))

# create a new dataframe
regions_venues_sorted = pd.DataFrame(columns=columns)
regions_venues_sorted['Region'] = berlin_regions_grouped['Region']

for ind in np.arange(berlin_regions_grouped.shape[0]):
    regions_venues_sorted.iloc[ind, 1:] = return_most_common_venues(berlin_regions_grouped.iloc[ind, :], num_top_venues)

regions_venues_sorted.set_index('Region', inplace=True)
regions_venues_sorted

1st Most Common Category 2nd Most Common Category  \
Region                                                     
0            Italian Restaurant                     Café   
1                          Café       Italian Restaurant   
2                          Café       Italian Restaurant   
3                          Café       Italian Restaurant   
4                        Bakery                     Café   
5                          Café    Vietnamese Restaurant   

       3rd Most Common Category 4th Most Common Category  \
Region                                                     
0                        Bakery        German Restaurant   
1                        Bakery         Asian Restaurant   
2                        Bakery              Pizza Place   
3             German Restaurant                   Bakery   
4            Italian Restaurant              Pizza Place   
5            Italian Restaurant                   Bakery   

       5th Most Common Category 6th Most Common Category  \
Region                                                     
0         Vietnamese Restaurant               Restaurant   
1         Vietnamese Restaurant        Indian Restaurant   
2             German Restaurant    Vietnamese Restaurant   
3         Vietnamese Restaurant               Restaurant   
4              Asian Restaurant             Burger Joint   
5                Breakfast Spot            Deli / Bodega   

       7th Most Common Category 8th Most Common Category  \
Region                                                     
0                  Burger Joint       Chinese Restaurant   
1                   Pizza Place                   Bistro   
2                    Restaurant       Turkish Restaurant   
3              Sushi Restaurant           Breakfast Spot   
4                Breakfast Spot    Vietnamese Restaurant   
5             German Restaurant              Pizza Place   

       9th Most Common Category      10th Most Common Category  
Region                                                          
0             Indian Restaurant              French Restaurant  
1              Sushi Restaurant              German Restaurant  
2             Indian Restaurant             Falafel Restaurant  
3                        Bistro  Vegetarian / Vegan Restaurant  
4           Fried Chicken Joint              Indian Restaurant  
5              Sushi Restaurant               Doner Restaurant

As can be seen, there seems to be a large similarity in popular categories between the regions.

As you may remember, regions #3 and #0 were the most populous clusters and, therefore, our foremost candidates. Let's just see these two clusters.

In [34]:
regions_venues_sorted.loc[[0,3]]

1st Most Common Category 2nd Most Common Category  \
Region                                                     
0            Italian Restaurant                     Café   
3                          Café       Italian Restaurant   

       3rd Most Common Category 4th Most Common Category  \
Region                                                     
0                        Bakery        German Restaurant   
3             German Restaurant                   Bakery   

       5th Most Common Category 6th Most Common Category  \
Region                                                     
0         Vietnamese Restaurant               Restaurant   
3         Vietnamese Restaurant               Restaurant   

       7th Most Common Category 8th Most Common Category  \
Region                                                     
0                  Burger Joint       Chinese Restaurant   
3              Sushi Restaurant           Breakfast Spot   

       9th Most Common Category      10th Most Common Category  
Region                                                          
0             Indian Restaurant              French Restaurant  
3                        Bistro  Vegetarian / Vegan Restaurant

We again see very similar representation of categories in these two regions. In fact, with a slight difference of order, the top 6 restaurant categories are exactly the same!

Before coming to a final decision, we can also inspect if there is a large discrepancy in less popular restaurant categories. To do this, we can find the standard deviations of frequency of occurrence for each category.

In [35]:
# Retrieve category std between regions 0 and 3
top2_comparison = berlin_regions_grouped.set_index('Region').loc[[0,3]].std()

# Sort results in descending order
top2_comparison.sort_values(ascending=False, axis=0, inplace=True)

# Name columns
top2_comparison = pd.DataFrame(data=top2_comparison, columns=["Standard Deviation"])

top2_comparison.head(10)

Standard Deviation
Italian Restaurant                  0.019758
Café                                0.017749
Restaurant                          0.016678
Bistro                              0.013680
Greek Restaurant                    0.011273
German Restaurant                   0.010295
Trattoria/Osteria                   0.009932
Chinese Restaurant                  0.009340
Turkish Restaurant                  0.009065
Mediterranean Restaurant            0.008040

The dataframe (in descending order of St.D.) shows relatively small deviations. We can confirm this by calculating the mean of the standard deviations.

In [36]:
print("The mean standard deviation between categories in regions #0 and #3 is", round(top2_comparison.mean()[0],5))

The mean standard deviation between categories in regions #0 and #3 is 0.0028


With a low mean of standard deviation between occurrences of categories between the two regions, we conclude that two candidate regions have a similar distribution of restaurant types.

We conclude that our best candidate for a local food distribution service in Berlin would be **Region #3** with the highest population.

### Thank you for reading!

This notebook was created by Ali Gündüz for the capstone project of the [*IBM Data Science Professional Certificate*](https://www.coursera.org/professional-certificates/ibm-data-science) program on Coursera.